In [ ]:
import pandas as pd
import numpy  as np

In [ ]:
#Read in the data
data = pd.read_csv("Market Data AUDJPY MA RSI Stoch  As Series.csv")
#Let's drop the last two years of data. We'll use that to validate our model in the back test
data = data.iloc[365:-(365 * 2),:]
data

Time    Open    High     Low   Close         MA  \
365   2000.02.11 00:00:00  68.640  69.440  68.360  68.610  68.763000   
366   2000.02.13 00:00:00  68.770  68.830  68.620  68.680  68.825750   
367   2000.02.14 00:00:00  68.680  68.760  68.070  68.210  68.867250   
368   2000.02.15 00:00:00  68.230  68.910  67.840  68.770  68.912750   
369   2000.02.16 00:00:00  68.770  69.260  68.720  69.060  68.957750   
...                   ...     ...     ...     ...     ...        ...   
7265  2022.06.22 00:00:00  94.869  94.919  93.588  93.902  92.282550   
7266  2022.06.23 00:00:00  93.901  94.165  92.645  93.058  92.306550   
7267  2022.06.24 00:00:00  93.057  94.022  92.780  93.850  92.386325   
7268  2022.06.26 00:00:00  93.747  94.064  93.452  93.786  92.471550   
7269  2022.06.27 00:00:00  93.786  93.943  92.972  93.735  92.566500   

            RSI    Stoch M    Stoch S  
365   51.330706  18.867925  42.006026  
366   51.644730   2.892562  22.449294  
367   49.429510   3.056769  12.753031  
368   51.968885  30.882353  21.817692  
369   53.227107  67.788462  44.803077  
...         ...        ...        ...  
7265  54.442732  74.699110  76.701621  
7266  52.018034  41.094148  58.897884  
7267  54.006509  22.176676  40.537280  
7268  53.820058  27.977177  34.257228  
7269  53.667322  49.193910  41.725569  

[6905 rows x 9 columns]

In [ ]:
#Difference In MA
data["Change in MA"] = data["MA"] - data["MA"].shift(40)

#RSI
data["Change in RSI"] = data["RSI"] - data["RSI"].shift(40)

#Stoch
data["Change in STO"] = data["Stoch M"] - data["Stoch M"].shift(40)

#MA States
data["MA 1"] = 0
data["MA 2"] = 0
data.loc[data["MA"] > data["MA"].shift(40),"MA 1"] = 1
data.loc[data["MA"] <= data["MA"].shift(40),"MA 2"] = 1

#Stoch States
data["STO 1"] = 0
data["STO 2"] = 0
data["STO 3"] = 0

data.loc[data["Stoch M"] > 80,"STO 1"] = 1
data.loc[data["Stoch M"] < 20,"STO 2"] = 1
data.loc[(data["Stoch M"] >= 20) & (data["Stoch M"] <= 70),"STO 3"] = 1

#RSI States
data["RSI 1"] = 0
data["RSI 2"] = 0
data["RSI 3"] = 0
data.loc[data["RSI"] < 30,"RSI 1"] = 1
data.loc[data["RSI"] > 70,"RSI 2"] = 1
data.loc[(data["RSI"] >= 30) & (data["RSI"] <= 70),"RSI 3"] = 1

#Difference in RSI
data["Change in RSI"] = data["RSI"] - data["RSI"].shift(40)

#Target
data["Target"]    = data["Close"].shift(-22) - data["Close"]
data["MA Target"] = data["MA"].shift(-22) - data["MA"]

#Clean up the data
data = data.dropna()
data = data.iloc[40:,:]
data = data.reset_index(drop=True)
data

Time    Open    High     Low   Close         MA  \
0     2000.05.15 00:00:00  63.310  63.340  62.410  62.650  63.218750   
1     2000.05.16 00:00:00  62.630  63.530  62.520  63.170  63.176500   
2     2000.05.17 00:00:00  63.160  63.210  61.870  62.060  63.168000   
3     2000.05.18 00:00:00  62.050  62.530  61.600  61.630  63.126000   
4     2000.05.19 00:00:00  61.660  62.390  60.940  61.430  63.065750   
...                   ...     ...     ...     ...     ...        ...   
6798  2022.05.27 00:00:00  90.220  91.019  89.990  90.995  91.731000   
6799  2022.05.29 00:00:00  90.904  91.226  90.828  91.109  91.671600   
6800  2022.05.30 00:00:00  91.103  92.001  90.949  91.926  91.634875   
6801  2022.05.31 00:00:00  91.928  92.527  91.581  92.465  91.610275   
6802  2022.06.01 00:00:00  92.465  93.617  92.424  93.317  91.608300   

            RSI     Stoch M    Stoch S  Change in MA  ...  MA 1  MA 2  STO 1  \
0     44.212506   34.972678  26.414399     -3.172750  ...     0     1      0   
1     46.469466   51.533742  38.974071     -3.119500  ...     0     1      0   
2     42.658497   26.219512  32.596791     -2.982750  ...     0     1      0   
3     41.301127   18.498660  25.547725     -2.888250  ...     0     1      0   
4     40.678338    0.000000  12.773863     -2.818000  ...     0     1      0   
...         ...         ...        ...           ...  ...   ...   ...    ...   
6798  51.865164   63.348837  53.107953      3.399275  ...     1     0      0   
6799  52.173262   86.731271  69.919612      3.070825  ...     1     0      1   
6800  54.339996  100.000000  84.959806      2.787750  ...     1     0      1   
6801  55.709414  100.000000  92.479903      2.503000  ...     1     0      1   
6802  57.779997  100.000000  96.239951      2.254275  ...     1     0      1   

      STO 2  STO 3  RSI 1  RSI 2  RSI 3  Target  MA Target  
0         0      1      0      0      1   0.310  -0.660000  
1         0      1      0      0      1  -0.420  -0.619500  
2         0      1      0      0      1   0.800  -0.599250  
3         1      0      0      0      1   2.160  -0.527750  
4         1      0      0      0      1   2.480  -0.447250  
...     ...    ...    ...    ...    ...     ...        ...  
6798      0      1      0      0      1   2.907   0.551550  
6799      0      0      0      0      1   1.949   0.634950  
6800      0      0      0      0      1   1.924   0.751450  
6801      0      0      0      0      1   1.321   0.861275  
6802      0      0      0      0      1   0.418   0.958200  

[6803 rows x 22 columns]

In [ ]:
from sklearn.linear_model import Ridge
from sklearn.model_selection import TimeSeriesSplit,cross_val_score

In [ ]:
tscv = TimeSeriesSplit(n_splits=5,gap=30)

In [ ]:
#Our model can suggest optimal ways of using the RSI indicator
#Our model has learned that on average price tends to fall the RSI reading is less than 30 and increases otherwises
model = Ridge()

model.fit(data.loc[:,["RSI 1","RSI 2","RSI 3"]] , data["Target"])

model.coef_

array([-0.19297857,  0.14816216,  0.04481641])

In [ ]:
#RSI state
np.mean(cross_val_score(Ridge(),data.loc[:,["RSI 1","RSI 2","RSI 3"]] , data["Target"],cv=tscv))

-0.025569914370219736

In [ ]:
#Our model can suggest optimal ways of using the RSI indicator
#Our model has learned that on average price tends to fall the RSI reading is less than 30 and increases otherwises
model = Ridge()

model.fit(data.loc[:,["MA 1","MA 2"]] , data["Target"])

model.coef_

array([-0.15572796,  0.15572796])

In [ ]:
#MA state
np.mean(cross_val_score(Ridge(),data.loc[:,["MA 1","MA 2"]] , data["Target"],cv=tscv))

-0.009645886983465935

In [ ]:
#Our model can suggest optimal ways of using the RSI indicator
#Our model has learned that on average price tends to fall the RSI reading is less than 30 and increases otherwises
model = Ridge()

model.fit(data.loc[:,["STO 1","STO 2","STO 3"]] , data["Target"])

model.coef_

array([0.05128996, 0.07837446, 0.03090845])

In [ ]:
#The stochastic oscilator state
np.mean(cross_val_score(Ridge(),data.loc[:,["STO 1","STO 2","STO 3"]] , data["Target"],cv=tscv))

-0.01445838525812202

In [ ]:
import onnx
from skl2onnx import convert_sklearn
from skl2onnx.common.data_types import FloatTensorType

In [ ]:
#First we will export the RSI model
rsi_model = Ridge()
rsi_model.fit(data.loc[:,['RSI 1','RSI 2','RSI 3']],data.loc[:,'Target'])

Ridge()

In [ ]:
#Finally we will export the MA model
ma_model = Ridge()
ma_model.fit(data.loc[:,['MA 1','MA 2']],data.loc[:,'MA Target'])

Ridge()

In [ ]:
initial_types = [('float_input', FloatTensorType([1, 3]))]
onnx.save(convert_sklearn(rsi_model,initial_types=initial_types,target_opset=12),"AUDJPY D1 RSI AI F22 P40.onnx")

In [ ]:
initial_types = [('float_input', FloatTensorType([1, 2]))]
onnx.save(convert_sklearn(ma_model,initial_types=initial_types,target_opset=12),"AUDJPY D1 MA AI F22 P40.onnx")